# RWKV v5 / embedding init-range 1e-01 / 4k

- 96 layers
- 1024 embedding size

Going through the modified memory training for v5 models, across various initial embedding model weights

**Note:** This project assumes you have the rwkv-infctx conda env setup

# Basic Setup

In [1]:
# First lets setup the various directories, and init the model
!mkdir -p ../../../../model/
!mkdir -p ../../../../datapath/
!mkdir -p ../../../../checkpoint/

In [2]:
# Additional dependencies for eval stuff
!pip install -q aiocsv aiofiles


[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: python3.11 -m pip install --upgrade pip


In [3]:
DEEPSPEED_STRAT="deepspeed_stage_1"
GPU_DEVICES="auto"
ENABLE_WANDB=True

# Layer count and embed dim to start with
LAYER_COUNT=96
EMBED_DIM=1024

# Wavnet compatibility?
RWKV_WAVENET_LAYERS=0

EMBED_SCALE=0.1
EMBED_SCALE_LABEL=str(EMBED_SCALE).replace(".", "_")

WANDB_PREFIX=f"v5-L{LAYER_COUNT}-D{EMBED_DIM}-E{EMBED_SCALE}"
FILENAME_PREFIX=f"v5-L{LAYER_COUNT}-D{EMBED_DIM}-E{EMBED_SCALE_LABEL}"

print("DEEPSPEED_STRAT:", DEEPSPEED_STRAT)
print("ENABLE_WANDB:", ENABLE_WANDB)
print("GPU_DEVICES:", GPU_DEVICES)

if ENABLE_WANDB:
    WANDB_MODE="online"
else:
    WANDB_MODE="disabled"

# Computing the notebook, and various paths
import os
NOTEBOOK_DIR=os.path.dirname(os.path.abspath("__file__"))
PROJECT_DIR=os.path.abspath(os.path.join(NOTEBOOK_DIR, "../../../../"))
TRAINER_DIR=os.path.abspath(os.path.join(PROJECT_DIR, "./RWKV-v5/"))
INFERENCE_DIR=os.path.abspath(os.path.join(PROJECT_DIR, "./RWKV-v5/"))

print("NOTEBOOK_DIR:", NOTEBOOK_DIR)
print("INFERENCE_DIR:", INFERENCE_DIR)
print("TRAINER_DIR:", TRAINER_DIR)
print("PROJECT_DIR:", PROJECT_DIR)

DEEPSPEED_STRAT: deepspeed_stage_1
ENABLE_WANDB: True
GPU_DEVICES: auto
NOTEBOOK_DIR: /actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-memory
INFERENCE_DIR: /actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/RWKV-v5
TRAINER_DIR: /actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/RWKV-v5
PROJECT_DIR: /actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer


In [4]:
# Download the model directly (stop gap till HF sync issues is resolved)
# !cd "{TRAINER_DIR}" && cd "../model/" && \
#     wget -nc "https://huggingface.co/rwkv-x-dev/rwkv-x-playground/resolve/main/experiment/rwkv-x-exp/v5-memory/{FILENAME_PREFIX}-mem-ctx-2k.pth"
!cd "{TRAINER_DIR}" && cd "../model/" && \
    wget -nc "https://huggingface.co/rwkv-x-dev/rwkv-x-playground/resolve/main/experiment/rwkv-x-exp/v5-memory/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/model/v5-L96-D1024-E0_1-mem-ctx-2k.pth"

!cd "{TRAINER_DIR}" && cd "../model/" && \
    ls -alh .

--2023-09-01 16:07:47--  https://huggingface.co/rwkv-x-dev/rwkv-x-playground/resolve/main/experiment/rwkv-x-exp/v5-memory/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/model/v5-L96-D1024-E0_1-mem-ctx-2k.pth
Resolving huggingface.co (huggingface.co)... 

18.165.122.30, 18.165.122.120, 18.165.122.101, ...
Connecting to huggingface.co (huggingface.co)|18.165.122.30|:443... connected.
HTTP request sent, awaiting response... 

302 Found
Location: https://cdn-lfs.huggingface.co/repos/2e/f7/2ef78555202aa92abdbdf476ce3d0fd5a8b15f7245edf0b80d4d30572355f30d/8ce9e4f8e10ab705b4705845936ac1ff97e2d060a5d29f1d209a510c59435b3c?response-content-disposition=attachment%3B+filename*%3DUTF-8%27%27v5-L96-D1024-E0_1-mem-ctx-2k.pth%3B+filename%3D%22v5-L96-D1024-E0_1-mem-ctx-2k.pth%22%3B&Expires=1693843667&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTY5Mzg0MzY2N319LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy5odWdnaW5nZmFjZS5jby9yZXBvcy8yZS9mNy8yZWY3ODU1NTIwMmFhOTJhYmRiZGY0NzZjZTNkMGZkNWE4YjE1ZjcyNDVlZGYwYjgwZDRkMzA1NzIzNTVmMzBkLzhjZTllNGY4ZTEwYWI3MDViNDcwNTg0NTkzNmFjMWZmOTdlMmQwNjBhNWQyOWYxZDIwOWE1MTBjNTk0MzViM2M%7EcmVzcG9uc2UtY29udGVudC1kaXNwb3NpdGlvbj0qIn1dfQ__&Signature=oRfsR7g8dO1aFa930WIR0FE%7EAVzdeWm8oO0uiNxjYyUyEkuvuP21JWmgxqm83rtmJuO9qhhl9xQgr29iKAYvk7NdLLGamvu0aSAybDUOvAD6IU5Lx-xd9Wpiu%7EoBDRCvqCUIWmCPjKFNjBIIYcmlPy7PCfSwLvaCvqHFOzKAIvAPLiw7t6vFni0IiRgVuaNRC0MWJ7ttIulWr-B1hVueEpKk6

108.157.214.31, 108.157.214.82, 108.157.214.46, ...
Connecting to cdn-lfs.huggingface.co (cdn-lfs.huggingface.co)|108.157.214.31|:443... connected.
HTTP request sent, awaiting response... 

200 OK
Length: 2825976699 (2.6G) [binary/octet-stream]
Saving to: ‘v5-L96-D1024-E0_1-mem-ctx-2k.pth’

          v5-L96-D1   0%[                    ]       0  --.-KB/s               

...

th                   98%[==================> ]   2.59G  67.7MB/s    eta 1s     

h                    99%[==================> ]   2.61G  67.9MB/s    eta 1s     

                     99%[==================> ]   2.62G  66.1MB/s    eta 0s     

v5-L96-D1024-E0_1-m 100%[===================>]   2.63G  66.4MB/s    in 40s     

2023-09-01 16:08:28 (66.6 MB/s) - ‘v5-L96-D1024-E0_1-mem-ctx-2k.pth’ saved [2825976699/2825976699]



total 2.7G
drwxr-xr-x  2 root root   54 Sep  1 16:07 .
drwxr-xr-x 19 root root 4.0K Sep  1 16:07 ..
-rw-r--r--  1 root root 2.7G Sep  1 08:04 v5-L96-D1024-E0_1-mem-ctx-2k.pth


## Tune 5 : Ramping up the ctx size (4096), memory training

- Tune 5: Mid ctx size (4096), Scaling up!

In [5]:
%%script bash

########################################
# Generate the required jsonl dataset
########################################

# Reset the dataset dir
mkdir -p ../dataset
rm -rf ../dataset/*.jsonl

# Generate the various datasets
echo "## Generating word reptition dataset ##"

#
# We reduce the training set for < 50 words - and shift the focus upwards
# (aka 50-100 token * 2 : ~100 - 250 token ctx len)
#
python ../memory_script/gen_limited_prompt_completion_jsonl.py ../dataset/word-2-count.jsonl 2 100 &
for i in {5..500..5} 
do
    python ../memory_script/gen_limited_prompt_completion_jsonl.py ../dataset/gen-word-$i-count.jsonl $i 100 & 
    python ../memory_script/shuffle_limited_prompt_completion_jsonl.py ../dataset/shuffle-word-$i-count.jsonl $i 1 & 
done

#
# Ramping up the 50+ - 2100 words dataset
# 
for i in {505..4000..5} 
do
    python ../memory_script/gen_limited_prompt_completion_jsonl.py ../dataset/gen-word-$i-count.jsonl $i 200 & 
    python ../memory_script/shuffle_limited_prompt_completion_jsonl.py ../dataset/shuffle-word-$i-count.jsonl $i 20 & 
done

wait
echo "## Done ##"

ls -alh ../dataset/

## Generating word reptition dataset ##


Generated JSONL file with - 2 max words, 100 samples - at ../dataset/word-2-count.jsonl


Generated JSONL file with - 5 max words, 100 samples - at ../dataset/gen-word-5-count.jsonl


Generated JSONL file with - 15 max words, 100 samples - at ../dataset/gen-word-15-count.jsonl


Generated a single JSONL file with 567 samples (1 token repeat) - 5 max words - at ../dataset/shuffle-word-5-count.jsonl


...

-rw-r--r--  1 root root  524K Sep  1 16:08 shuffle-word-980-count.jsonl


-rw-r--r--  1 root root  521K Sep  1 16:08 shuffle-word-985-count.jsonl


-rw-r--r--  1 root root  520K Sep  1 16:08 shuffle-word-990-count.jsonl


-rw-r--r--  1 root root  523K Sep  1 16:08 shuffle-word-995-count.jsonl


-rw-r--r--  1 root root   13K Sep  1 16:08 word-2-count.jsonl


In [6]:
# Start the finetune model training
!cd "{TRAINER_DIR}" && \
    export WANDB_MODE="{WANDB_MODE}" && \
    export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
    python lightning_trainer.py fit \
        -c "{NOTEBOOK_DIR}/config-mem-template.yaml" \
        --trainer.logger.init_args.name="{WANDB_PREFIX} - Mem-Tune ctx-4k (train-ctx=4k, {DEEPSPEED_STRAT})" \
        --trainer.strategy="{DEEPSPEED_STRAT}" \
        --trainer.devices="{GPU_DEVICES}"  \
        --trainer.callbacks.init_args.dirpath="../checkpoint/{FILENAME_PREFIX}-mem-ctx-4k/" \
        --model.lr_init=3e-4 \
        --model.lr_final=1e-4 \
        --data.max_token_size=4096 \
        --model.ctx_len=4096 \
        --model.bptt_learning_range=1 \
        --model.load_model="../model/{FILENAME_PREFIX}-mem-ctx-2k.pth"

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'


/usr/local/lib/python3.11/dist-packages/lightning/pytorch/cli.py:484: UserWarning: LightningCLI's args parameter is intended to run from within Python like if it were from the command line. To prevent mistakes it is not recommended to provide both args and command line arguments, got: sys.argv[1:]=['fit', '-c', '/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-memory/config-mem-template.yaml', '--trainer.logger.init_args.name=v5-L96-D1024-E0.1 - Mem-Tune ctx-4k (train-ctx=4k, deepspeed_stage_1)', '--trainer.strategy=deepspeed_stage_1', '--trainer.devices=auto', '--trainer.callbacks.init_args.dirpath=../checkpoint/v5-L96-D1024-E0_1-mem-ctx-4k/', '--model.lr_init=3e-4', '--model.lr_final=1e-4', '--data.max_token_size=4096', '--model.ctx_len=4096', '--model.bptt_learning_range=1', '--model.load_model=../model/v5-L96-D1024-E0_1-mem-ctx-2k.pth'], args=['fit', '-c', '/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experime

/usr/local/lib/python3.11/dist-packages/lightning/fabric/utilities/seed.py:39: UserWarning: No seed found, seed set to 1010560597
  rank_zero_warn(f"No seed found, seed set to {seed}")
Global seed set to 1010560597


wandb: Currently logged in as: picocreator (rwkv-x-dev). Use `wandb login --relogin` to force relogin


...


Validation DataLoader 0: 100%|██████████████████| 16/16 [00:15<00:00,  1.02it/s]

Epoch 0: 100%|█| 15423/15423 [13:17:02<00:00,  3.10s/it, v_num=ufwn, train/loss=
Epoch 0: 100%|█| 15423/15423 [13:17:02<00:00,  3.10s/it, v_num=ufwn, train/loss=

`Trainer.fit` stopped: `max_epochs=1` reached.
Epoch 0: 100%|█| 15423/15423 [13:17:15<00:00,  3.10s/it, v_num=ufwn, train/loss=


wandb: Waiting for W&B process to finish... (success).


wandb: 
wandb: Run history:
wandb:              batchidx ▁▁▁▂▂▂▂▂▂▃▃▃▃▃▃▄▄▄▄▄▅▅▅▅▅▅▆▆▆▆▆▇▇▇▇▇▇███
wandb:                 epoch ▁▁▁▁▁▁▁▁▁▁
wandb:           global_rank ▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁
wandb:          real_ctx_len ▄▄▇▅▇▂▆▃▄█▂▆▅▁▅▇▃▄▄█▄▅▄▄▃▄▂▅▅▇▃▇▂▃▅▆█▆▄▇
wandb:               substep ▁▁▁▂▂▂▂▂▂▃▃▃▃▃▃▄▄▄▄▄▅▅▅▅▅▅▆▆▆▆▆▇▇▇▇▇▇███
wandb:            train/loss █▅▆▄▄▁▃▃▃▂▂▂▁▂▂▂▃▁▁▁▁▁▁▁▂▁▁▁▁▂▁▂▁▁▁▂▁▁▁▁
wandb:   trainer/global_step ▁▁▁▂▂▂▂▂▂▃▃▃▃▃▃▄▄▄▄▄▅▅▅▅▅▅▆▆▆▆▆▇▇▇▇▇▇███
wandb: trainer/learning_rate ███▇▇▇▇▇▇▆▆▆▆▆▆▅▅▅▅▅▄▄▄▄▄▄▃▃▃▃▃▂▂▂▂▂▂▁▁▁
wandb:       validation/loss ▁
wandb: 
wandb: Run summary:
wandb:              batchidx 15
wandb:                 epoch 0
wandb:           global_rank 0
wandb:          real_ctx_len 4064
wandb:               substep 120
wandb:            train/loss 0.90625
wandb:   trainer/global_step 481
wandb: trainer/learning_rate 0.0001
wandb:       validation/loss 0.21994
wandb: 
wandb: 🚀 View run v5-L96-D1024-E0.1 - Mem-Tune ctx-4k (train-ctx=4k, de

In [7]:
# Lets export the model from the checkpoint
!cd "{TRAINER_DIR}" && \
    python export_checkpoint.py \
        "../checkpoint/{FILENAME_PREFIX}-mem-ctx-4k/last.ckpt" \
        "../model/{FILENAME_PREFIX}-mem-ctx-4k.pth" "bf16"
!cd "{TRAINER_DIR}" && ls -alh "../model/{FILENAME_PREFIX}-mem-ctx-4k.pth"

Setting ds_accelerator to cuda (auto detect)


Processing zero checkpoint '../checkpoint/v5-L96-D1024-E0_1-mem-ctx-4k/last.ckpt/checkpoint'


Detected checkpoint of type zero stage ZeroStageEnum.optimizer_states, world_size: 8


Parsing checkpoint created by deepspeed==0.9.3


Reconstructed fp32 state dict with 1926 params 1412678656 elements
Saving bf16 state dict to ../model/v5-L96-D1024-E0_1-mem-ctx-4k.pth


-rw-r--r-- 1 root root 2.7G Sep  2 05:35 ../model/v5-L96-D1024-E0_1-mem-ctx-4k.pth


In [8]:
# Lets do a quick memory test
!export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
        python3 ../memory_script/eval_v5_memory_guided.py "{PROJECT_DIR}/model/{FILENAME_PREFIX}-mem-ctx-4k.pth"

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'


###
### Model validation start ###
###


## Model validation for 5 tokens : 100.0% similarity, with 5 matched token, and 0 token mismatch


## Model validation for 10 tokens : 100.0% similarity, with 10 matched token, and 0 token mismatch


...

## Model validation for 850 tokens : 96.35294117647058% similarity, with 819 matched token, and 31 token mismatch


## Model validation for 900 tokens : 96.33333333333334% similarity, with 867 matched token, and 33 token mismatch


## Model validation for 950 tokens : 96.94736842105263% similarity, with 921 matched token, and 29 token mismatch


## Model validation for 1000 tokens : 96.5% similarity, with 965 matched token, and 35 token mismatch


###
### Model validation end ###
###
